# Задача
Используя набор данных 'Wine':
* Построить классификаторы по методу ближайших соседей по парам признаков; (выбрать три пары признаков) и визуализируйте на какие области разбивается плоскоть;
* Построить классификаторы по методу ближайших соседей по наиболее информативным главным компонентам;
* Оценить точность классификаторов.

Строить классификаторы по 3,5,7 ближайшим соседям.


In [1]:
import numpy as np
import pandas as pd

import matplotlib.pyplot as plt
%matplotlib inline

from sklearn import neighbors, metrics, decomposition

In [2]:
attrs = """class_id
Alcohol
Malic acid
Ash
Alcalinity of ash
Magnesium
Total phenols
Flavanoids
Nonflavanoid phenols
Proanthocyanins
Color intensity
Hue
OD280/OD315 of diluted wines
Proline""".split('\n')
wine_df = pd.read_csv("data/wine.data", sep=",", names = attrs)
print(wine_df)

     class_id  Alcohol  Malic acid   Ash  Alcalinity of ash  Magnesium  \
0           1    14.23        1.71  2.43               15.6        127   
1           1    13.20        1.78  2.14               11.2        100   
2           1    13.16        2.36  2.67               18.6        101   
3           1    14.37        1.95  2.50               16.8        113   
4           1    13.24        2.59  2.87               21.0        118   
5           1    14.20        1.76  2.45               15.2        112   
6           1    14.39        1.87  2.45               14.6         96   
7           1    14.06        2.15  2.61               17.6        121   
8           1    14.83        1.64  2.17               14.0         97   
9           1    13.86        1.35  2.27               16.0         98   
10          1    14.10        2.16  2.30               18.0        105   
11          1    14.12        1.48  2.32               16.8         95   
12          1    13.75        1.73  2.

In [3]:
clf_u = neighbors.KNeighborsClassifier(n_neighbors=7, weights='uniform')
clf_d = neighbors.KNeighborsClassifier(n_neighbors=7, weights='distance')

In [4]:
X1 = wine_df[attrs[1]].values
X2 = wine_df[attrs[2]].values
X=np.c_[X1,X2]  
Y = wine_df["class_id"].values

In [5]:
clf_u.fit(X,Y)
clf_d.fit(X,Y)

KNeighborsClassifier(algorithm='auto', leaf_size=30, metric='minkowski',
           metric_params=None, n_jobs=1, n_neighbors=7, p=2,
           weights='distance')

In [6]:
Y_u = clf_u.predict(X)
Y_d = clf_d.predict(X)

In [7]:
print("uniform", metrics.accuracy_score(Y,Y_u))
print("distance", metrics.accuracy_score(Y,Y_d))

uniform 0.837078651685
distance 1.0


In [8]:
x1_min, x1_max = X1.min(), X1.max()
x2_min, x2_max = X2.min(), X2.max()
x1 = np.linspace(x1_min, x1_max, 100)
x2 = np.linspace(x2_min, x2_max, 100)
xx1, xx2 = np.meshgrid(x1,x2)
XX = np.c_[xx1.ravel(), xx2.ravel()]
ZZ_u = clf_u.predict(XX)
ZZ_d = clf_d.predict(XX)
ZZ_u = np.reshape(ZZ_u, xx1.shape)
ZZ_d = np.reshape(ZZ_d, xx1.shape)

In [9]:
plt.figure(figsize=(16.0,16.0))
plt.winter()
plt.subplot(2,2,1)
plt.title('uniform')
plt.imshow(ZZ_u, extent = [x1_min, x1_max, x2_min, x2_max], origin='bottom', aspect='auto')
plt.grid(1)
plt.subplot(2,2,3)
plt.title('distance')
plt.imshow(ZZ_d, extent = [x1_min, x1_max, x2_min, x2_max], origin='bottom', aspect='auto')
plt.grid(1)
plt.subplot(2,2,2)
plt.title('uniform')
plt.imshow(ZZ_u, extent = [x1_min, x1_max, x2_min, x2_max], origin='bottom', aspect='auto')
plt.scatter(X1, X2, s=36, c=Y)
plt.xlabel(attrs[1])
plt.ylabel(attrs[2])
plt.grid(1)
plt.subplot(2,2,4)
plt.title('distance')
plt.imshow(ZZ_d, extent = [x1_min, x1_max, x2_min, x2_max], origin='bottom', aspect='auto')
plt.scatter(X1, X2, s=36, c=Y)
plt.xlabel(attrs[1])
plt.ylabel(attrs[2])
plt.grid(1)

In [10]:
cols = tuple([wine_df[attr].values for attr in attrs[1:]])
X = np.c_[cols]
Y = wine_df["class_id"].values

In [11]:
print(X.shape, Y.shape)

(178, 13) (178,)


In [12]:
pca = decomposition.PCA()
pca.fit(X)

PCA(copy=True, iterated_power='auto', n_components=None, random_state=None,
  svd_solver='auto', tol=0.0, whiten=False)

In [13]:
plt.figure(figsize=(10,10))
plt.bar(range(13), pca.explained_variance_ratio_)
plt.show()
print(pca.explained_variance_ratio_)

[  9.98091230e-01   1.73591562e-03   9.49589576e-05   5.02173562e-05
   1.23636847e-05   8.46213034e-06   2.80681456e-06   1.52308053e-06
   1.12783044e-06   7.21415811e-07   3.78060267e-07   2.12013755e-07
   8.25392788e-08]


In [14]:
pca.n_components = 2
U = pca.fit_transform(X)

In [15]:
clf = neighbors.KNeighborsClassifier(n_neighbors=5, weights='distance')
clf.fit(U,Y)

KNeighborsClassifier(algorithm='auto', leaf_size=30, metric='minkowski',
           metric_params=None, n_jobs=1, n_neighbors=5, p=2,
           weights='distance')

In [16]:
XX = np.c_[xx1.ravel(), xx2.ravel()]
ZZ = clf.predict(XX)
ZZ = np.reshape(ZZ, xx1.shape)

In [17]:
plt.figure(figsize=(12.0,8.0))
plt.winter()
plt.title('distance')
plt.imshow(ZZ_d, extent = [x1_min, x1_max, x2_min, x2_max], origin='bottom', aspect='auto')
plt.scatter(X1, X2,s=35, c=Y)
plt.grid(1)